In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/llm-finetuning


In [3]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/llm-finetuning/.env


True

In [4]:
import os

model_name = os.getenv("MODEL_NAME")
token = os.getenv("HF_TOKEN") or None
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
local_model = os.getenv("LOCAL_MODEL")
hub_model = os.getenv("HUB_MODEL")
num_train_epochs = int(os.getenv("NUM_TRAIN_EPOCHS") or 0)
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")

max_seq_length = 2048  # Choose any! We auto support RoPE Scaling internally!
dtype = (
    None  # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
)

model_name, load_in_4bit, local_model, hub_model, max_seq_length, num_train_epochs, dtype, data_path, results_path

('unsloth/Qwen2-0.5B-Instruct',
 True,
 None,
 None,
 2048,
 6,
 None,
 'datasets/mac/mac.tsv',
 'results/mac-results_lf-r2.csv')

In [5]:
!nvidia-smi

Thu Jul  4 11:06:16 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 545.23.07              Driver Version: 546.12       CUDA Version: 12.3     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA GeForce RTX 4080 ...    On  | 00000000:01:00.0 Off |                  N/A |
| N/A   52C    P8               3W / 150W |    355MiB / 12282MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [6]:
from llm_toolkit.translation_engine import load_translation_dataset

dataset = load_translation_dataset(data_path)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


[nltk_data] Downloading package wordnet to /home/inflaton/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /home/inflaton/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/inflaton/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


loading /home/inflaton/code/projects/courses/llm-finetuning/llm_toolkit/translation_engine.py
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})


In [7]:
df = dataset["train"].to_pandas()

In [8]:
import pandas as pd

df_alpaca = pd.DataFrame({"instruction": ["Please translate the following Chinese text into English and provide only the translated content, nothing else."]*len(df)})

In [9]:
df_alpaca["input"] = df["chinese"]
df_alpaca["output"] = df["english"]
df_alpaca

instruction  \
0     Please translate the following Chinese text in...   
1     Please translate the following Chinese text in...   
2     Please translate the following Chinese text in...   
3     Please translate the following Chinese text in...   
4     Please translate the following Chinese text in...   
...                                                 ...   
4523  Please translate the following Chinese text in...   
4524  Please translate the following Chinese text in...   
4525  Please translate the following Chinese text in...   
4526  Please translate the following Chinese text in...   
4527  Please translate the following Chinese text in...   

                                                  input  \
0                                              全仗着狐仙搭救。   
1         过后，表哥告诉她俩，这人是导演，在外国留过学的，还会编剧，今天拍的这戏，就是他自编自导的。   
2                             这凤姐忽然想起一件事来，便向窗外叫：“蓉儿回来！”   
3     三个老红卫兵走到叶文洁面前，面对着她站成了一排——当年，她们也是这样面对叶哲泰的——试图再现...   
4                         程先生照单全收，都是一个“谢”字，然后问王琦瑶有什么话说。   
...                                                 ...   
4523                      外边有两张腿歪面裂的八仙桌子，桌旁胡乱搡着几条狭窄的木凳。   
4524                                       贾瑞听了，喜的抓耳挠腮。   
4525                     听了这样的评价，我们心情激动，和大家一起振臂高呼：打倒王二！   
4526                                       海老公道：“记住了吗？”   
4527                                       上面说，这样写缺少细节。   

                                                 output  
0               Because I was protected by a fox fairy.  
1     He was the director, the cousin later told the...  
2     Xi-feng suddenly seemed to remember something,...  
3     The three old Red Guards stood in front of Ye ...  
4     Mr. Cheng accepted their toast with equanimity...  
...                                                 ...  
4523  Two rickety tables with scarred tops and a few...  
4524  At this last remark Jia Rui positively scratch...  
4525  Hearing comments like this, our emotions were ...  
4526                           'Can you remember that?'  
4527  This time the opinions from above said it need...  

[4528 rows x 3 columns]

In [10]:
df_alpaca.to_json(
    "llama-factory/data/alpaca_mac.json", orient="records", lines=False, indent=2
)

In [11]:
df = pd.read_json("llama-factory/data/alpaca_mac.json", orient="records", lines=False)

In [12]:
df.head()

instruction  \
0  Please translate the following Chinese text in...   
1  Please translate the following Chinese text in...   
2  Please translate the following Chinese text in...   
3  Please translate the following Chinese text in...   
4  Please translate the following Chinese text in...   

                                               input  \
0                                           全仗着狐仙搭救。   
1      过后，表哥告诉她俩，这人是导演，在外国留过学的，还会编剧，今天拍的这戏，就是他自编自导的。   
2                          这凤姐忽然想起一件事来，便向窗外叫：“蓉儿回来！”   
3  三个老红卫兵走到叶文洁面前，面对着她站成了一排——当年，她们也是这样面对叶哲泰的——试图再现...   
4                      程先生照单全收，都是一个“谢”字，然后问王琦瑶有什么话说。   

                                              output  
0            Because I was protected by a fox fairy.  
1  He was the director, the cousin later told the...  
2  Xi-feng suddenly seemed to remember something,...  
3  The three old Red Guards stood in front of Ye ...  
4  Mr. Cheng accepted their toast with equanimity...

In [13]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 5.39 ms, sys: 19.5 ms, total: 24.9 ms
Wall time: 527 ms


In [16]:
%%time

!./scripts/tune-lf.sh config/qwen2_0.5b_lora_sft.yaml

Current Directory:
/home/inflaton/code/projects/courses/llm-finetuning/llama-factory
07/04/2024 11:09:05 - INFO - llamafactory.hparams.parser - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, compute dtype: torch.bfloat16
[INFO|tokenization_utils_base.py:2161] 2024-07-04 11:09:06,545 >> loading file vocab.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/vocab.json
[INFO|tokenization_utils_base.py:2161] 2024-07-04 11:09:06,545 >> loading file merges.txt from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/merges.txt
[INFO|tokenization_utils_base.py:2161] 2024-07-04 11:09:06,545 >> loading file tokenizer.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/tokenizer.json
[INFO|tokenization_utils_base.py

In [17]:
%%time

!./scripts/tune-lf.sh config/qwen2_1.5b_lora_sft.yaml

loading /home/inflaton/code/projects/courses/llm-finetuning/llm_toolkit/translation_engine.py
Current Directory:
/home/inflaton/code/projects/courses/llm-finetuning/llama-factory
07/04/2024 12:22:59 - INFO - llamafactory.hparams.parser - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, compute dtype: torch.bfloat16
[INFO|tokenization_utils_base.py:2161] 2024-07-04 12:23:00,122 >> loading file vocab.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snapshots/ba1cf1846d7df0a0591d6c00649f57e798519da8/vocab.json
[INFO|tokenization_utils_base.py:2161] 2024-07-04 12:23:00,122 >> loading file merges.txt from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snapshots/ba1cf1846d7df0a0591d6c00649f57e798519da8/merges.txt
[INFO|tokenization_utils_base.py:2161] 2024-07-04 12:23:00,122 >> loading file tokenizer.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snap

In [19]:
%%time

!./scripts/tune-lf.sh config/qwen2_7b_lora_sft_unsloth.yaml

Current Directory:
/home/inflaton/code/projects/courses/llm-finetuning/llama-factory
07/04/2024 14:50:13 - WARNING - llamafactory.hparams.parser - We recommend enable `upcast_layernorm` in quantized training.
07/04/2024 14:50:13 - INFO - llamafactory.hparams.parser - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, compute dtype: torch.bfloat16
[INFO|tokenization_utils_base.py:2161] 2024-07-04 14:50:14,466 >> loading file vocab.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-7B-Instruct/snapshots/41c66b0be1c3081f13defc6bdf946c2ef240d6a6/vocab.json
[INFO|tokenization_utils_base.py:2161] 2024-07-04 14:50:14,466 >> loading file merges.txt from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-7B-Instruct/snapshots/41c66b0be1c3081f13defc6bdf946c2ef240d6a6/merges.txt
[INFO|tokenization_utils_base.py:2161] 2024-07-04 14:50:14,466 >> loading file tokenizer.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen

In [20]:
%%time

!./scripts/tune-lf.sh config/qwen2_1.5b_lora_sft_unsloth.yaml

Current Directory:
/home/inflaton/code/projects/courses/llm-finetuning/llama-factory
07/04/2024 21:56:42 - WARNING - llamafactory.hparams.parser - We recommend enable `upcast_layernorm` in quantized training.
07/04/2024 21:56:42 - INFO - llamafactory.hparams.parser - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, compute dtype: torch.bfloat16
[INFO|tokenization_utils_base.py:2161] 2024-07-04 21:56:42,789 >> loading file vocab.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snapshots/ba1cf1846d7df0a0591d6c00649f57e798519da8/vocab.json
[INFO|tokenization_utils_base.py:2161] 2024-07-04 21:56:42,789 >> loading file merges.txt from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snapshots/ba1cf1846d7df0a0591d6c00649f57e798519da8/merges.txt
[INFO|tokenization_utils_base.py:2161] 2024-07-04 21:56:42,789 >> loading file tokenizer.json from cache at /home/inflaton/.cache/huggingface/hub/models--

In [22]:
%%time

!./scripts/tune-lf.sh config/qwen2_0.5b_lora_sft_unsloth.yaml

Current Directory:
/home/inflaton/code/projects/courses/llm-finetuning/llama-factory
07/05/2024 06:15:40 - WARNING - llamafactory.hparams.parser - We recommend enable `upcast_layernorm` in quantized training.
07/05/2024 06:15:40 - INFO - llamafactory.hparams.parser - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, compute dtype: torch.bfloat16
[INFO|tokenization_utils_base.py:2161] 2024-07-05 06:15:40,695 >> loading file vocab.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/vocab.json
[INFO|tokenization_utils_base.py:2161] 2024-07-05 06:15:40,695 >> loading file merges.txt from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/merges.txt
[INFO|tokenization_utils_base.py:2161] 2024-07-05 06:15:40,695 >> loading file tokenizer.json from cache at /home/inflaton/.cache/huggingface/hub/models--